# 1. Diseño esquema




## Describe las entidades y campos clave del dataset (tipos de datos, llaves, nulabilidad).

### - Entidad de Dimensión: DATOS_USUARIOS  
Información básica del paciente.

| Campo en Español      | Campo en Inglés | Tipo   | Llave | Nulabilidad | Descripción |
|-----------------------|-----------------|--------|--------|-------------|-------------|
| ID del usuario        | usuario_id      | INT    | PK     | NOT NULL    | Identificador único del paciente. |
| Nombre                | name            | STRING | -      | NOT NULL    | Nombre completo del paciente. |
| Edad                  | age             | INT    | -      | NOT NULL    | Edad del paciente. |
| Género                | gender          | STRING | -      | NOT NULL    | Género del paciente. |
| Tipo de sangre        | blood_type      | STRING | -      | NOT NULL    | Grupo sanguíneo del paciente. |



### - Entidad de Dimensión: INFORMACION_CLINICA  
Describe la información clínica del paciente durante su estancia.

| Campo en Español      | Campo en Inglés   | Tipo   | Llave | Nulabilidad | Descripción |
|-----------------------|-------------------|--------|--------|-------------|-------------|
| ID del usuario        | usuario_id        | INT    | FK     | NOT NULL    | Referencia al paciente. |
| Fecha de admisión     | admission_date    | DATE   | -      | NOT NULL    | Fecha en que se admitió al paciente. |
| Doctor asignado       | doctor            | STRING | -      | NOT NULL    | Médico responsable. |
| Hospital              | hospital          | STRING | -      | NOT NULL    | Hospital donde se atiende al paciente. |
| Tipo de admisión      | admission_type    | STRING | -      | NOT NULL    | Motivo y modalidad de ingreso. |
| Número de habitación  | room_number       | STRING | -      | NOT NULL    | Habitación asignada al paciente. |
| Condición médica      | medical_condition | STRING | -      | NOT NULL    | Diagnóstico clínico principal. |
| Medicamento           | medication        | STRING | -      | NOT NULL    | Medicamento administrado. |
| Fecha de alta         | discharge_date    | DATE   | -      | NOT NULL    | Salida del paciente. |



### - Entidad de Hechos: FACTURACION  
Contiene los montos facturados para cada proceso clínico.

| Campo en Español    | Campo en Inglés      | Tipo   | Llave | Nulabilidad | Descripción |
|---------------------|-----------------------|--------|--------|-------------|-------------|
| ID de factura       | factura_id            | INT    | PK     | NOT NULL    | Identificador único de factura. |
| ID de admisión      | admission_id          | INT    | FK     | NOT NULL    | Referencia al proceso clínico. |
| Seguro proveedor    | insurance_provider    | STRING | -      | NOT NULL    | Entidad aseguradora. |
| Monto facturado     | billing_amount        | DOUBLE | -      | NOT NULL    | Valor facturado. |

## DDL (Spark SQL)

[Archivo DDL](DDL.sql)


## Diagrama

![ERD HospitalSS](Diagrama.png)









# 2. Configura y evidencia la infraestructura en Databricks CE

## Configuración de Databricks

En Databricks Community Edition (CE) algunas opciones avanzadas no están
disponibles (como autoscaling, selección de tipos de nodo o múltiples
workers).\
Por ello, la configuración que se muestra corresponde a los parámetros
realmente visibles o consultables desde el entorno.



## 2.1 Crear y configurar el clúster

1.  En la barra lateral izquierda, navegar a **Compute**.
2.  Clic en **Create Cluster**.
3.  En Databricks CE, solo se pueden definir parámetros básicos. La
    configuración resultante del clúster es:

-   **Cluster Name:** `cluster_hospitalSS`
-   **Databricks Runtime Version:** versión disponible por defecto (en
    este caso, Spark 4.0.0 según el notebook)
-   **Python Version:** 3.12.3
-   **Cluster Mode:** *Single Node* (fijo en CE)
-   **Autoscaling:** No disponible
-   **Núcleos / Memoria:** valores asignados automáticamente por
    Databricks CE

4.  Finalmente, clic en **Create cluster**.

La creación del clúster habilita el entorno requerido para ejecutar
Spark, SQL y Python sobre Databricks.



## 2.2 Versiones de Python y Spark

Para evidenciar las versiones del entorno, se ejecutó el siguiente
código:

``` python
# Celda Python – mostrar versiones
import sys

print("Versión de Spark:", spark.version)
print("Versión de Python:", sys.version.splitlines()[0])
```

### Salida obtenida:

    Versión de Spark: 4.0.0
    Versión de Python: 3.12.3 (main, Aug 14 2025, 17:47:21) [GCC 13.3.0]

También se consultan configuraciones del clúster mediante:

``` python
for item in spark.sparkContext.getConf().getAll():
    print(item)
```

Sin embargo, debido a las limitaciones de Databricks CE, las
especificaciones completas del hardware del nodo no pueden recuperarse
totalmente, por lo que se reportan únicamente las versiones de Spark y
Python obtenidas directamente.



## 2.3 Estructura de almacenamiento

El almacenamiento del proyecto se gestiona mediante **DBFS (Databricks
File System)**.

Las rutas principales empleadas son:

-   `/FileStore/`
-   `/databricks-datasets/`
-   Directorios creados manualmente para el proyecto.

En este caso, se utilizó el directorio:

    /FileStore/datasets/

para almacenar y cargar el dataset proveniente de Kaggle.

### Ejemplo de verificación:

``` python
display(dbutils.fs.ls("/FileStore/datasets"))
```

Este comando permite confirmar la presencia de archivos dentro de DBFS y
validar correctamente la estructura de almacenamiento.




# 3. Obtén datos de Kaggle y crea una tabla

In [0]:
!pip install kagglehub[pandas-datasets]>=0.3.8

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


## Descarga librerias

In [0]:
import os
import zipfile
import kagglehub
import pandas as pd

## dataset (Kaggle)

In [0]:
def download_dataset_zip(url = ""):
        print("Descargando dataset desde Kaggle...")
        dataset_path = kagglehub.dataset_download(url)
        print("Ruta al dataset:", dataset_path)
        return dataset_path
    
def extract_zip_files(dataset_path):
        zip_files = [f for f in os.listdir(dataset_path) if f.endswith('.zip')]
        if zip_files:
            zip_file = os.path.join(dataset_path, zip_files[0])
            extract_dir = os.path.join(dataset_path, "extracted")
            os.makedirs(extract_dir, exist_ok=True)
            print(f"Extrayendo {zip_file} en {extract_dir}...")
            with zipfile.ZipFile(zip_file, "r") as z:
                z.extractall(extract_dir)
            return extract_dir
        else:
            # Si no se encuentra un ZIP, se verifica si existen archivos CSV en la ruta
            csv_files = [f for f in os.listdir(dataset_path) if f.endswith('.csv')]
            if csv_files:
                print("No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.")
                return dataset_path
            else:
                raise FileNotFoundError("No se encontró ningún archivo .zip ni archivos .csv en la ruta del dataset")

def create_csv(csv_dir):
        #os.makedirs('src/static/csv', exist_ok=True)
        csv_files = [f for f in os.listdir(csv_dir) if f.endswith('.csv')]
        if not csv_files:
            raise FileNotFoundError("No se encontraron archivos CSV en el directorio extraído")

        for file in csv_files:
            file_path = os.path.join(csv_dir, file)
            print(f"Leyendo {file_path}...")
            try:
                df = pd.read_csv(file_path, encoding="latin1")
            except Exception as e:
                print(f"Error al leer {file}: {e}")
                continue
            print(f"Creando/actualizando ")
        print("cvs creado correctamente en ")
        return df

## - dataset seleccionado:
https://www.kaggle.com/datasets/prasad22/healthcare-dataset

In [0]:
import pandas as pd
df = pd.DataFrame()
dataset = download_dataset_zip("prasad22/healthcare-dataset") 
csv_dir =extract_zip_files(dataset)
df = create_csv(csv_dir)



Descargando dataset desde Kaggle...
Ruta al dataset: /home/spark-44710525-730b-4766-9e97-12/.cache/kagglehub/datasets/prasad22/healthcare-dataset/versions/2
No se encontró archivo ZIP pero se detectaron archivos CSV; se asume que el dataset ya se encuentra extraído.
Leyendo /home/spark-44710525-730b-4766-9e97-12/.cache/kagglehub/datasets/prasad22/healthcare-dataset/versions/2/healthcare_dataset.csv...
Creando/actualizando 
cvs creado correctamente en 


In [0]:
df.head()



Name  Age  Gender  ... Discharge Date   Medication  Test Results
0  Bobby JacksOn   30    Male  ...     2024-02-02  Paracetamol        Normal
1   LesLie TErRy   62    Male  ...     2019-08-26    Ibuprofen  Inconclusive
2    DaNnY sMitH   76  Female  ...     2022-10-07      Aspirin        Normal
3   andrEw waTtS   28  Female  ...     2020-12-18    Ibuprofen      Abnormal
4  adrIENNE bEll   43  Female  ...     2022-10-09   Penicillin      Abnormal

[5 rows x 15 columns]

In [0]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 55500 entries, 0 to 55499
Data columns (total 15 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Name                55500 non-null  object 
 1   Age                 55500 non-null  int64  
 2   Gender              55500 non-null  object 
 3   Blood Type          55500 non-null  object 
 4   Medical Condition   55500 non-null  object 
 5   Date of Admission   55500 non-null  object 
 6   Doctor              55500 non-null  object 
 7   Hospital            55500 non-null  object 
 8   Insurance Provider  55500 non-null  object 
 9   Billing Amount      55500 non-null  float64
 10  Room Number         55500 non-null  int64  
 11  Admission Type      55500 non-null  object 
 12  Discharge Date      55500 non-null  object 
 13  Medication          55500 non-null  object 
 14  Test Results        55500 non-null  object 
dtypes: float64(1), int64(2), object(12)
memory usage: 6.4

## creacion catalogo

In [0]:
%sql
-- 1. Crear el Catálogo principal (si no existe)
CREATE CATALOG IF NOT EXISTS hospitalSS;

-- 2. Crear el Esquema de Ventas (base de datos)
CREATE SCHEMA IF NOT EXISTS hospitalSS.datos_usuario_schema;

-- 3. Crear el Volume para almacenar archivos no tabulares,

CREATE VOLUME IF NOT EXISTS hospitalSS.datos_usuario_schema.vol_usuario;

## Convertir df de pandas a Spark 

In [0]:
spark_df = spark.createDataFrame(df)
spark_df.show(5)

+-------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+
|         Name|Age|Gender|Blood Type|Medical Condition|Date of Admission|          Doctor|            Hospital|Insurance Provider|    Billing Amount|Room Number|Admission Type|Discharge Date| Medication|Test Results|
+-------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+
|Bobby JacksOn| 30|  Male|        B-|           Cancer|       2024-01-31|   Matthew Smith|     Sons and Miller|        Blue Cross|18856.281305978155|        328|        Urgent|    2024-02-02|Paracetamol|      Normal|
| LesLie TErRy| 62|  Male|        A+|          Obesity|       2019-08-20| Samantha Davies|             Kim Inc|          Medicare|33

## Creación de la Tabla con Spark

In [0]:
spark_df = spark_df.toDF(*[c.strip().lower().replace(" ", "_") for c in spark_df.columns])
spark_df.write.mode("overwrite").saveAsTable( "hospitalSS.datos_usuario_schema.tbl_datos_usuarios_spk")

## Descrpcion de la tabla

In [0]:
%sql
DESCRIBE TABLE hospitalSS.datos_usuario_schema.tbl_datos_usuarios_spk;


col_name data_type comment name string null age bigint null gender string null blood_type string null medical_condition string null date_of_admission string null doctor string null hospital string null insurance_provider string null billing_amount double null room_number bigint null admission_type string null discharge_date string null medication string null test_results string null

## Datos de la tabla creada con spark


In [0]:
# 1. Cargamos la tabla creada en Spark a un DataFrame
df_usuarios = spark.table("hospitalSS.datos_usuario_schema.tbl_datos_usuarios_spk")

# 2. Seleccionamos solo las columnas de tipo numérico (double, int, long)
#    Estas son las que permiten operaciones estadísticas
numeric_cols = [
    f.name for f in df_usuarios.schema
    if f.dataType.typeName() in ('double', 'decimal', 'float', 'integer', 'long')
]

print("Columnas numéricas detectadas:", numeric_cols)

# 3. Creamos un DataFrame solo con esas columnas y aplicamos describe()
df_numeric_stats = df_usuarios.select(*numeric_cols)

# 4. Mostramos los resultados
display(df_numeric_stats.describe())


Columnas numéricas detectadas: ['age', 'billing_amount', 'room_number']


summary age billing_amount room_number count 55500 55500 55500 mean 51.53945945945946 25539.316097211813 301.1348288288288 stddev 19.602453808514348 14211.454430864418 115.2430687009733 min 13 -2008.4921398591305 101 max 89 52764.276736469175 500

## Validaccion tabla creada

In [0]:
%sql
SHOW TABLES IN hospitalSS.datos_usuario_schema;


database tableName isTemporary datos_usuario_schema tbl_datos_usuarios_spk false

In [0]:
%sql
SELECT COUNT(*) AS total_registros
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_spk;


total_registros 55500

In [0]:
%sql
CREATE VOLUME IF NOT EXISTS hospitalSS.datos_usuario_schema.vol_usuario;


In [0]:
%sql
LIST '/Volumes/hospitalSS/datos_usuario_schema/vol_usuario/';


path name size modification_time /Volumes/hospitalSS/datos_usuario_schema/vol_usuario/healthcare_dataset.csv healthcare_dataset.csv 8869649 1763919602000

## Carga de datos en Spark

In [0]:
# Ruta del archivo dentro del volume
ruta_csv_volume = 'dbfs:/Volumes/hospitalSS/datos_usuario_schema/vol_usuario/healthcare_dataset.csv'
# Leer la data desde el volume sin crear tabla Delta todavía
df_diagnostico = spark.read.csv(
    ruta_csv_volume,
    header=True,        # La primera fila contiene los nombres de las columnas
    inferSchema=True    # Spark detecta automáticamente los tipos de datos
)

display(df_diagnostico.columns)


_1 Id;Name;Age;Gender;Blood Type;Medical Condition;Date of Admission;Doctor;Hospital;Insurance Provider;Billing Amount;Room Number;Admission Type;Discharge Date;Medication;Test Results

## Persistencia


In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW raw_csv_view
USING CSV
OPTIONS (
  path '/Volumes/hospitalSS/datos_usuario_schema/vol_usuario/healthcare_dataset.csv',
  header 'true',
  inferSchema 'true',
  sep ';'
);
DESCRIBE raw_csv_view;


col_name data_type comment Id int null Name string null Age int null Gender string null Blood Type string null Medical Condition string null Date of Admission date null Doctor string null Hospital string null Insurance Provider string null Billing Amount string null Room Number int null Admission Type string null Discharge Date date null Medication string null Test Results string null

## Creación de la Tabla con SQL

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW raw_csv_clean AS
SELECT
    Id,
    Name,
    Age,
    Gender,
    `Blood Type`        AS Blood_Type,
    `Medical Condition` AS Medical_Condition,
    `Date of Admission` AS Date_Admission,
    Doctor,
    Hospital,
    `Insurance Provider` AS Insurance_Provider,
    `Billing Amount`     AS Billing_Amount,
    `Room Number`        AS Room_Number,
    `Admission Type`     AS Admission_Type,
    `Discharge Date`     AS Discharge_Date,
    Medication,
    `Test Results`       AS Test_Results
FROM raw_csv_view;

CREATE TABLE IF NOT EXISTS hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql
AS SELECT *
FROM raw_csv_clean;



num_affected_rows num_inserted_rows

In [0]:
%sql
SELECT COUNT(*)
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql;



COUNT(*) 55500

# 4. Validaciones Spark - SQL 

### Spark 


In [0]:
# Ver esquema (metadatos)
df = spark.table("hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql")
df.printSchema()


root
 |-- Id: integer (nullable = true)
 |-- Name: string (nullable = true)
 |-- Age: integer (nullable = true)
 |-- Gender: string (nullable = true)
 |-- Blood_Type: string (nullable = true)
 |-- Medical_Condition: string (nullable = true)
 |-- Date_Admission: date (nullable = true)
 |-- Doctor: string (nullable = true)
 |-- Hospital: string (nullable = true)
 |-- Insurance_Provider: string (nullable = true)
 |-- Billing_Amount: string (nullable = true)
 |-- Room_Number: integer (nullable = true)
 |-- Admission_Type: string (nullable = true)
 |-- Discharge_Date: date (nullable = true)
 |-- Medication: string (nullable = true)
 |-- Test_Results: string (nullable = true)



In [0]:
# Vista previa de datos
display(df)

Id Name Age Gender Blood_Type Medical_Condition Date_Admission Doctor Hospital Insurance_Provider Billing_Amount Room_Number Admission_Type Discharge_Date Medication Test_Results 1 Bobby JacksOn 30 Male B- Cancer 2024-01-31 Matthew Smith Sons and Miller Blue Cross 18.856.281.305.978.100 328 Urgent 2024-02-02 Paracetamol Normal 2 LesLie TErRy 62 Male A+ Obesity 2019-08-20 Samantha Davies Kim Inc Medicare 33.643.327.286.577.800 265 Emergency 2019-08-26 Ibuprofen Inconclusive 3 DaNnY sMitH 76 Female A- Obesity 2022-09-22 Tiffany Mitchell Cook PLC Aetna 27.955.096.078.842.400 205 Emergency 2022-10-07 Aspirin Normal 4 andrEw waTtS 28 Female O+ Diabetes 2020-11-18 Kevin Wells Hernandez Rogers and Vang, Medicare 3.790.978.240.987.520 450 Elective 2020-12-18 Ibuprofen Abnormal 5 adrIENNE bEll 43 Female AB+ Cancer 2022-09-19 Kathleen Hanna White-White Aetna 14.238.317.813.937.600 458 Urgent 2022-10-09 Penicillin Abnormal 6 EMILY JOHNSOn 36 Male A+ Asthma 2023-12-20 Taylor Newton Nunez-Humphrey UnitedHealthcare 4.814.511.095.104.180 389 Urgent 2023-12-24 Ibuprofen Normal 7 edwArD EDWaRDs 21 Female AB- Diabetes 2020-11-03 Kelly Olson Group Middleton Medicare 1.958.087.234.486.090 389 Emergency 2020-11-15 Paracetamol Inconclusive 8 CHrisTInA MARtinez 20 Female A+ Cancer 2021-12-28 Suzanne Thomas Powell Robinson and Valdez, Cigna 4.582.046.272.159.450 277 Emergency 2022-01-07 Paracetamol Inconclusive 9 JASmINe aGuIlaR 82 Male AB+ Asthma 2020-07-01 Daniel Ferguson Sons Rich and Cigna 50.119.222.791.548.500 316 Elective 2020-07-14 Aspirin Abnormal 10 ChRISTopher BerG 58 Female AB- Cancer 2021-05-23 Heather Day Padilla-Walker UnitedHealthcare 1.978.463.106.221.070 249 Elective 2021-06-22 Paracetamol Inconclusive 11 mIchElLe daniELs 72 Male O+ Cancer 2020-04-19 John Duncan Schaefer-Porter Medicare 12.576.795.609.050.200 394 Urgent 2020-04-22 Paracetamol Normal 12 aaRon MARtiNeZ 38 Female A- Hypertension 2023-08-13 Douglas Mayo Lyons-Blair Medicare 7.999.586.879.604.180 288 Urgent 2023-09-05 Lipitor Inconclusive 13 connOR HANsEn 75 Female A+ Diabetes 2019-12-12 Kenneth Fletcher Powers Miller, and Flores Cigna 4.328.228.335.770.430 134 Emergency 2019-12-28 Penicillin Abnormal 14 rObeRt bAuer 68 Female AB+ Asthma 2020-05-22 Theresa Freeman Rivera-Gutierrez UnitedHealthcare 33.207.706.633.729.600 309 Urgent 2020-06-19 Lipitor Normal 15 bROOkE brady 44 Female AB+ Cancer 2021-10-08 Roberta Stewart Morris-Arellano UnitedHealthcare 40.701.599.227.308.700 182 Urgent 2021-10-13 Paracetamol Normal 16 MS. nAtalIE gAMble 46 Female AB- Obesity 2023-01-01 Maria Dougherty Cline-Williams Blue Cross 12.263.357.425.021.300 465 Elective 2023-01-11 Aspirin Inconclusive 17 haley perkins 63 Female A+ Arthritis 2020-06-23 Erica Spencer Cervantes-Wells UnitedHealthcare 24.499.847.903.736.500 114 Elective 2020-07-14 Paracetamol Normal 18 mRS. jamiE cAMPBELl 38 Male AB- Obesity 2020-03-08 Justin Kim Torres, and Harrison Jones Cigna 17.440.465.444.124.600 449 Urgent 2020-04-02 Paracetamol Abnormal 19 LuKE BuRgEss 34 Female A- Hypertension 2021-03-04 Justin Moore Jr. Houston PLC Blue Cross 1.884.302.301.783.410 260 Elective 2021-03-14 Aspirin Abnormal 20 dANIEL schmIdt 63 Male B+ Asthma 2022-11-15 Denise Galloway Hammond Ltd Cigna 23.762.203.579.059.500 465 Elective 2022-11-22 Penicillin Normal 21 tIMOTHY burNs 67 Female A- Asthma 2023-06-28 Krista Smith Jones LLC Blue Cross 425.145.885.533.243 115 Elective 2023-07-02 Aspirin Normal 22 ChRISToPHEr BRiGhT 48 Male B+ Asthma 2020-01-21 Gregory Smith Williams-Davis Aetna 17.695.911.622.343.800 295 Urgent 2020-02-09 Lipitor Normal 23 KatHRYn StewArt 58 Female O+ Arthritis 2022-05-12 Vanessa Newton Clark-Mayo Aetna 599.810.290.819.591 327 Urgent 2022-06-10 Lipitor Inconclusive 24 dR. EilEEn thomPsoN 59 Male A+ Asthma 2021-08-02 Donna Martinez MD and Sons Smith Aetna 25.250.052.428.216.100 119 Urgent 2021-08-12 Lipitor Inconclusive 25 PAUl hEndERsOn 72 Female AB+ Hypertension 2020-05-15 Stephanie Kramer Wilson Group Medicare 3.3

In [0]:
# Estadísticas descriptivas
df.describe().show()


+-------+------------------+------------+------------------+------+----------+-----------------+-------------+--------------------+------------------+--------------------+-----------------+--------------+----------+------------+
|summary|                Id|        Name|               Age|Gender|Blood_Type|Medical_Condition|       Doctor|            Hospital|Insurance_Provider|      Billing_Amount|      Room_Number|Admission_Type|Medication|Test_Results|
+-------+------------------+------------+------------------+------+----------+-----------------+-------------+--------------------+------------------+--------------------+-----------------+--------------+----------+------------+
|  count|             55500|       55500|             55500| 55500|     55500|            55500|        55500|               55500|             55500|               55500|            55500|         55500|     55500|       55500|
|   mean|           27750.5|        NULL| 51.53945945945946|  NULL|      NULL|      

In [0]:
#Conteo total de registros
df.count()


55500

In [0]:
# Conteo por género (validación de distribución)
df.groupBy("Gender").count().show()


+------+-----+
|Gender|count|
+------+-----+
|  Male|27774|
|Female|27726|
+------+-----+



In [0]:
# Conteo por tipo de sangre
df.groupBy("Blood_Type").count().orderBy("count", ascending=False).show()


+----------+-----+
|Blood_Type|count|
+----------+-----+
|        A-| 6969|
|        A+| 6956|
|       AB+| 6947|
|        B+| 6945|
|       AB-| 6945|
|        B-| 6944|
|        O+| 6917|
|        O-| 6877|
+----------+-----+



In [0]:
# Top 10 pacientes por monto facturado
df.orderBy(df.Billing_Amount.desc()).limit(10).show()


+-----+------------------+---+------+----------+-----------------+--------------+-------------------+--------------------+------------------+-------------------+-----------+--------------+--------------+-----------+------------+
|   Id|              Name|Age|Gender|Blood_Type|Medical_Condition|Date_Admission|             Doctor|            Hospital|Insurance_Provider|     Billing_Amount|Room_Number|Admission_Type|Discharge_Date| Medication|Test_Results|
+-----+------------------+---+------+----------+-----------------+--------------+-------------------+--------------------+------------------+-------------------+-----------+--------------+--------------+-----------+------------+
|18526|         jo hUNteR| 43|Female|        B+|          Obesity|    2021-02-15|Mrs. Destiny Garcia|   Velasquez-Wilkins|        Blue Cross|999.451.194.291.205|        401|     Emergency|    2021-03-14|Paracetamol|    Abnormal|
|36224|mR. robeRt waLlAcE| 84|Female|        B+|          Obesity|    2022-05-05|   

In [0]:
# Validación de valores nulos
from pyspark.sql.functions import col, sum

df.select([ sum(col(c).isNull().cast("int")).alias(c) for c in df.columns ]).show()


+---+----+---+------+----------+-----------------+--------------+------+--------+------------------+--------------+-----------+--------------+--------------+----------+------------+
| Id|Name|Age|Gender|Blood_Type|Medical_Condition|Date_Admission|Doctor|Hospital|Insurance_Provider|Billing_Amount|Room_Number|Admission_Type|Discharge_Date|Medication|Test_Results|
+---+----+---+------+----------+-----------------+--------------+------+--------+------------------+--------------+-----------+--------------+--------------+----------+------------+
|  0|   0|  0|     0|         0|                0|             0|     0|       0|                 0|             0|          0|             0|             0|         0|           0|
+---+----+---+------+----------+-----------------+--------------+------+--------+------------------+--------------+-----------+--------------+--------------+----------+------------+



### SQL

In [0]:
%sql
DESCRIBE TABLE hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql;

col_name data_type comment Id int null Name string null Age int null Gender string null Blood_Type string null Medical_Condition string null Date_Admission date null Doctor string null Hospital string null Insurance_Provider string null Billing_Amount string null Room_Number int null Admission_Type string null Discharge_Date date null Medication string null Test_Results string null

In [0]:
%sql
SHOW CREATE TABLE hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql;


createtab_stmt CREATE TABLE hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql (
 Id INT,
 Name STRING,
 Age INT,
 Gender STRING,
 Blood_Type STRING,
 Medical_Condition STRING,
 Date_Admission DATE,
 Doctor STRING,
 Hospital STRING,
 Insurance_Provider STRING,
 Billing_Amount STRING,
 Room_Number INT,
 Admission_Type STRING,
 Discharge_Date DATE,
 Medication STRING,
 Test_Results STRING)
USING delta
COLLATION 'UTF8_BINARY'
TBLPROPERTIES (
 'delta.enableDeletionVectors' = 'true',
 'delta.feature.appendOnly' = 'supported',
 'delta.feature.deletionVectors' = 'supported',
 'delta.feature.invariants' = 'supported',
 'delta.minReaderVersion' = '3',
 'delta.minWriterVersion' = '7',
 'delta.parquet.compression.codec' = 'zstd')

In [0]:
%sql
SELECT COUNT(*) AS total_registros
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql;




total_registros 55500

In [0]:
%sql
SELECT * 
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql
LIMIT 10;


Id Name Age Gender Blood_Type Medical_Condition Date_Admission Doctor Hospital Insurance_Provider Billing_Amount Room_Number Admission_Type Discharge_Date Medication Test_Results 1 Bobby JacksOn 30 Male B- Cancer 2024-01-31 Matthew Smith Sons and Miller Blue Cross 18.856.281.305.978.100 328 Urgent 2024-02-02 Paracetamol Normal 2 LesLie TErRy 62 Male A+ Obesity 2019-08-20 Samantha Davies Kim Inc Medicare 33.643.327.286.577.800 265 Emergency 2019-08-26 Ibuprofen Inconclusive 3 DaNnY sMitH 76 Female A- Obesity 2022-09-22 Tiffany Mitchell Cook PLC Aetna 27.955.096.078.842.400 205 Emergency 2022-10-07 Aspirin Normal 4 andrEw waTtS 28 Female O+ Diabetes 2020-11-18 Kevin Wells Hernandez Rogers and Vang, Medicare 3.790.978.240.987.520 450 Elective 2020-12-18 Ibuprofen Abnormal 5 adrIENNE bEll 43 Female AB+ Cancer 2022-09-19 Kathleen Hanna White-White Aetna 14.238.317.813.937.600 458 Urgent 2022-10-09 Penicillin Abnormal 6 EMILY JOHNSOn 36 Male A+ Asthma 2023-12-20 Taylor Newton Nunez-Humphrey UnitedHealthcare 4.814.511.095.104.180 389 Urgent 2023-12-24 Ibuprofen Normal 7 edwArD EDWaRDs 21 Female AB- Diabetes 2020-11-03 Kelly Olson Group Middleton Medicare 1.958.087.234.486.090 389 Emergency 2020-11-15 Paracetamol Inconclusive 8 CHrisTInA MARtinez 20 Female A+ Cancer 2021-12-28 Suzanne Thomas Powell Robinson and Valdez, Cigna 4.582.046.272.159.450 277 Emergency 2022-01-07 Paracetamol Inconclusive 9 JASmINe aGuIlaR 82 Male AB+ Asthma 2020-07-01 Daniel Ferguson Sons Rich and Cigna 50.119.222.791.548.500 316 Elective 2020-07-14 Aspirin Abnormal 10 ChRISTopher BerG 58 Female AB- Cancer 2021-05-23 Heather Day Padilla-Walker UnitedHealthcare 1.978.463.106.221.070 249 Elective 2021-06-22 Paracetamol Inconclusive

In [0]:
%sql
SELECT Gender, COUNT(*) AS total
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql
GROUP BY Gender;



Gender total Male 27774 Female 27726

In [0]:
%sql
SELECT *
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql
ORDER BY Billing_Amount DESC
LIMIT 10;


Id Name Age Gender Blood_Type Medical_Condition Date_Admission Doctor Hospital Insurance_Provider Billing_Amount Room_Number Admission_Type Discharge_Date Medication Test_Results 18526 jo hUNteR 43 Female B+ Obesity 2021-02-15 Mrs. Destiny Garcia Velasquez-Wilkins Blue Cross 999.451.194.291.205 401 Emergency 2021-03-14 Paracetamol Abnormal 36224 mR. robeRt waLlAcE 84 Female B+ Obesity 2022-05-05 Natalie Moore Clark Ltd UnitedHealthcare 998.506.121.369.566 171 Urgent 2022-05-20 Paracetamol Inconclusive 40100 krisTY FlOwerS 66 Female O+ Arthritis 2021-11-09 Ryan Campbell and Brown, Robinson Davis Blue Cross 997.469.273.394.406 373 Urgent 2021-11-13 Ibuprofen Normal 45885 Gregory gILes 62 Male A+ Diabetes 2020-02-12 Mary Brown LLC Clark UnitedHealthcare 996.936.473.115.436 478 Elective 2020-02-16 Aspirin Inconclusive 53447 Gregory gILes 57 Male A+ Diabetes 2020-02-12 Mary Brown LLC Clark UnitedHealthcare 996.936.473.115.436 478 Elective 2020-02-16 Aspirin Inconclusive 32903 shANE HernAndeZ 46 Female A- Arthritis 2024-04-26 Pamela Hughes Smith-Ward Blue Cross 996.049.488.343.805 489 Emergency 2024-05-23 Paracetamol Inconclusive 1746 jEnNifEr BeNsOn 21 Male B- Hypertension 2024-01-29 Maureen Salazar Tucker-Brown Medicare 995.544.142.848.513 413 Elective 2024-02-26 Ibuprofen Abnormal 36204 kAreN ho 56 Male A+ Hypertension 2019-09-27 Melanie Hunter Inc Dillon UnitedHealthcare 995.487.227.140.092 477 Emergency 2019-10-19 Paracetamol Normal 3713 ROGER MeRRiTt 52 Female AB- Obesity 2020-05-22 David Costa Washington-Carter UnitedHealthcare 995.163.009.929.675 313 Emergency 2020-06-08 Paracetamol Abnormal 2657 joHn CasTrO 62 Male AB- Arthritis 2019-07-29 Brandy Burns LLC Gardner Aetna 993.881.926.740.808 138 Emergency 2019-08-19 Ibuprofen Abnormal

In [0]:
%sql
SELECT Blood_Type, COUNT(*) AS total
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql
GROUP BY Blood_Type
ORDER BY total DESC;


Blood_Type total A- 6969 A+ 6956 AB+ 6947 B+ 6945 AB- 6945 B- 6944 O+ 6917 O- 6877

In [0]:
%sql
SELECT 
  COUNT(*) - COUNT(Id) AS null_Id,
  COUNT(*) - COUNT(Name) AS null_Name,
  COUNT(*) - COUNT(Age) AS null_Age,
  COUNT(*) - COUNT(Gender) AS null_Gender
  -- agrega más campos si quieres
FROM hospitalSS.datos_usuario_schema.tbl_datos_usuarios_sql;


null_Id null_Name null_Age null_Gender 0 0 0 0

- Metadatos:
Validamos la estructura del dataset para confirmar que Spark interpretó correctamente los tipos de datos.
En Spark: df.printSchema()
En SQL: DESCRIBE TABLE

- Descripción de datos:
Usamos df.describe().show() y funciones SQL (AVG, MIN, MAX) para verificar rangos y valores esperados.

- Consultas SELECT y GROUP BY
Ejecutamos en Spark y SQL los mismos agrupamientos (por género, tipo de sangre, etc.) para validar que los datos cargados coinciden entre motor SQL y PySpark.

- Conteos y muestras
Verificamos que el número de registros coincide entre Spark y SQL (df.count() y SELECT COUNT(*)).
También mostramos los 10 primeros registros para validar formato y calidad de datos.

# 5. Ventajas y desventajas: SQL vs Spark


| Característica | SQL | Spark (PySpark) |
|----------------|-----|------------------|
| **Facilidad de uso** | Muy intuitivo para consultas directas sobre tablas (`SELECT`, `GROUP BY`, `COUNT`). Perfecto para validaciones rápidas tras la carga en Delta. | Requiere conocer APIs (`spark.read`, `.select()`, `.withColumn()`, `.groupBy()`). Ideal para manipulación previa al guardado. |
| **Ingesta desde Volumes / CSV** | SQL depende de `USING CSV OPTIONS (...)`, pero la vista creada no permite ver fácilmente problemas en los datos. | Permite inspección profunda antes de crear tablas (`df.show()`, `df.printSchema()`, `df.describe()`). Detecta tipos automáticamente con `inferSchema=True`. |
| **Limpieza y transformación de columnas** | Renombrar columnas debe hacerse manualmente con `AS`, útil cuando ya conoces todos los nombres. | Mucho más flexible: se pueden transformar múltiples columnas con expresiones, regex o loops antes de persistir. |
| **Creación de tablas gestionadas (Delta)** | Muy directo: `CREATE TABLE AS SELECT`. Ideal para persistencia final. | También puede persistir con `.write.saveAsTable()`, pero requiere mayor detalle en particiones y modos. |
| **Validaciones después de ingesta** | `DESCRIBE TABLE`, `SHOW CREATE TABLE`, `COUNT(*)`, filtros y agregaciones rápidas. | `df.describe()`, `df.dtypes`, `df.groupBy().count()`, `.filter()`. Más capacidades estadísticas y de profiling. |
| **Rendimiento en grandes volúmenes** | Bueno en datasets moderados, pero puede degradar con millones de registros. | Diseñado para big data. Optimiza con ejecución distribuida, cache, particiones y Catalyst Optimizer. |
| **Integración con BI** | Excelente: Power BI, Excel, Tableau lo consumen fácilmente. | No es consumo directo; Spark se usa para ETL previo a la capa de presentación. |
| **Diagnóstico y errores** | Mensajes claros y más fáciles de interpretar. | Errores más técnicos: memoria, particiones, shuffles. Requiere interpretación más avanzada. |
| **Curva de aprendizaje** | Muy baja; cualquiera puede empezar rápido. | Más alta; se necesita entender transformación distribuida y conceptos de Spark. |
